Libraries

In [2]:
import os
from mistralai import Mistral
from dotenv import load_dotenv
import pandas as pd
load_dotenv()
import time
from pymongo import MongoClient
import json
import asyncio


Env and client setup

In [3]:

api_key = os.environ["mistral_key"]
gen_ai_key = os.environ["gen_ai_key"]
agent_id = os.environ["agent_id"]
db_url = os.environ["DB_URL"]
model = "open-mistral-nemo"
client = Mistral(api_key=api_key)
mongo_client = MongoClient(db_url)
db  = mongo_client.reddit
post_db = db['post_new']

Load Data from MonogoDB

In [4]:
rec = post_db.find()
rec = list(rec)
print(rec[0]) 

{'_id': ObjectId('67558db3eeb7770cf0a37c63'), 'id': '1h9gtbi', 'title': 'Do you think this startup is worth continuing?', 'selftext': "1,006 people came to my app and I made 9 sales. My product is $9.99 and it's a one-time payment. My profit rate is 90%. Do you think this is a good rate or is it not worth continuing? I haven't done any advertising so far, I just made 2 reddit posts without naming the app and in the comments they asked for the name of the app and I posted the link. Do you think I should advertise to influencers? I need help.", 'ups': 1, 'subreddit': 'startups', 'created_utc': 1733656859.0, 'num_comments': 6, 'url': 'https://www.reddit.com/r/startups/comments/1h9gtbi/do_you_think_this_startup_is_worth_continuing/', 'response': 'question'}


Local Data import

In [ ]:
df = pd.read_csv('startups_hot.csv')
df2 = df[['title','selftext']]
df3 = df2[['title','selftext']][:20]
col = list(df.columns)

Update Records in mongodb

In [58]:
def update_post(post):
    try:
        post_db.update_one({'id':post['id']},{'$set':{'response':post['response']}},upsert=True)
        # print(f'Post updated [{post["id"]}]')
    except Exception as e:
        print(e)

Basic Classification with Mistral

create chunks

In [5]:
def split_list(data, chunk_size):
    return [data[i:i + chunk_size] for i in range(0, len(data), chunk_size)]

chunks = split_list(rec, 25)
for chunk in chunks:
    post_ids = [post['id'] for post in chunk]
    print(post_ids)
    print()

['1h9gtbi', '1h9e0an', '1h9cua9', '1h9bzig', '1h9achm', '1h9ac56', '1h980yx', '1h96sie', '1h96sbl', '1h96d8c', '1h965rt', '1h94vta', '1h94egx', '1h9347e', '1h92zk6', '1h91q7g', '1h913zy', '1h90nxb', '1h8wpup', '1h8wajl', '1h8u5d3', '1h8tnov', '1h8tgei', '1h8ss1k', '1h8r9fp']

['1h8qq7b', '1h8pt5k', '1h8prw9', '1h8mm84', '1h8kbbb', '1h8jv31', '1h8iw8c', '1h8ivih', '1h8iqv1', '1h8h50y', '1h8glkz', '1h8g50t', '1h8cue9', '1h8cmw5', '1h8b5hh', '1h8b1ik', '1h8b03i', '1h8aj0a', '1h892yq', '1h88f75', '1h87kt3', '1h87a6u', '1h85pcu', '1h848tt', '1h829qs']

['1h81uv4', '1h813eu', '1h80z8i', '1h7z0oa', '1h7yvru', '1h7x1in', '1h7vtze', '1h7ups3', '1h7sz7d', '1h7swwh', '1h7qtzb', '1h7pwsc', '1h7o9vp', '1h7naik', '1h7na49', '1h7lbr2', '1h7kz6j', '1h7kb2v', '1h7k5e0', '1h7jhe7', '1h7h4re', '1h7g55b', '1h7f9zv', '1h7eo7c', '1h7dvkr']

['1h7aic5', '1h7a4sa', '1h74irl', '1h745jt', '1h71115', '1h6zf4y', '1h6yt0d', '1h6xbny', '1h6vx4p', '1h6vhar', '1h6rslq', '1h6rank', '1h6r9vv', '1h6pm9q', '1h6nfv4', '1h

In [58]:
rec[1]['id']

'1h9e0an'

In [34]:
count = 0
for i in rec:
    chat_response = client.agents.complete(
        agent_id=agent_id,
        messages=[
            {
                "role": "user",
                "content": f"post_id:{i['id']},title: {i['title']},body: {i['selftext']}" ,
            },
        ],
    )
    response = eval(chat_response.choices[0].message.content)
    i['response'] = response['flag']
    update_post(i)    
    print(response)
    count += 1
    print(f'{count}. title:{i["title"]},response:{response["flag"]}')

{'post_id': '1h9gtbi', 'flag': 'question'}
1. title:Do you think this startup is worth continuing?,response:question
{'post_id': '1h9e0an', 'flag': 'experience'}
2. title:Finally launched my LinkedIn AI chatbot!,response:experience
{'post_id': '1h9cua9', 'flag': 'experience'}
3. title:Finally!! I launched it after months ,response:experience
{'post_id': '1h9bzig', 'flag': 'question'}
4. title:Struggling with Low Conversions? Here’s How Startup-Specific Copy Can Help,response:question
{'post_id': '1h9achm', 'flag': 'question'}
5. title:Im so impatient and its killing me,response:question
{'post_id': '1h9ac56', 'flag': 'question'}
6. title: How do you validate your business ideas? ,response:question
{'post_id': '1h980yx', 'flag': 'question'}
7. title:What’s expected of an AI-powered SMM tool?,response:question
{'post_id': '1h96sie', 'flag': 'question'}
8. title:Seeking Lightmatter and OpenAI Shares – Willing to Explore Secondary Opportunities,response:question
{'post_id': '1h96sbl', 'fla

KeyboardInterrupt: 

In [8]:
response = eval(response)
print(len(response))

25


In [ ]:
remains=[]
count = 0
for chunk in chunks: #400 records
    chat_response = client.agents.complete(
    agent_id=agent_id,
    messages=[
        {
            "role": "user",
            "content": str([f"post_id:{i['id']},title: {i['title']},body: {i['selftext']}" for i in chunk]), #25 records
        },
    ],
     response_format = {
          "type": "json_object",
      }
)
    try:
        response = eval(chat_response.choices[0].message.content)
        post_res = {i['post_id']:i['flag'] for i in response}
    except:
        post_res = {}
    for i in chunk:
        i['response'] = post_res.get(i['id'],'no_response')
        update_post(i)   
    count += 1
    if post_res == {}:
        remains.append(chunk)
        print(f'Batch {count} failed')
    else:
        print(f'Batch {count} completed')
    time.sleep(2)

Batch 1 completed
Batch 2 completed
Batch 3 completed
Batch 4 failed
Batch 5 completed
Batch 6 completed
Batch 7 completed
Batch 8 completed
Batch 9 completed
Batch 10 completed
Batch 11 completed
Batch 12 completed
Batch 13 completed
Batch 14 completed
Batch 15 completed
Batch 16 completed
Batch 17 completed
Batch 18 completed
Batch 19 completed
Batch 20 failed
Batch 21 completed
Batch 22 completed
Batch 23 completed
Batch 24 completed
Batch 25 completed
Batch 26 failed
Batch 27 completed
Batch 28 completed
Batch 29 completed
Batch 30 completed
Batch 31 completed
Batch 32 failed
Batch 33 completed
Batch 34 completed
Batch 35 completed
Batch 36 completed
Batch 37 failed
Batch 38 completed
Batch 39 completed
Batch 40 failed
Batch 41 completed
Batch 42 completed
Batch 43 completed
Batch 44 completed
Batch 45 completed
Batch 46 completed
Batch 47 completed
Batch 48 completed
Batch 49 completed
Batch 50 completed
Batch 51 completed
Batch 52 completed
Batch 53 completed
Batch 54 completed
B

[{'_id': ObjectId('67558db3eeb7770cf0a37cae'),
  'id': '1h7aic5',
  'title': "My friend's dad passed away and i am trying to help him.",
  'selftext': "Hey Reddit, I’m here hoping to get some guidance from this amazing community.\n\nA close friend of mine recently lost his father, and it’s been devastating for their family. His dad was involved in the alco-bev industry for over 20 years, co-running a company with a few partners. He wasn’t the technical guy, and played a key role in sales and relationships.\n\nAfter his passing, the other founders have been trying to push my friend out of the company. It’s heartbreaking to see him struggle like this, especially since he now has the huge responsibility of providing for his family.\n\nHe’s trying to start his own business in the same field, focusing on importing Vatted Malt Spirit (VMS) from Scotland to India. The thing is, he doesn't know much about how this supply chain works or how to even get started. But he wants to continue in this 

In [ ]:
async def response_gen(post,agent_id):
    chat_response = client.agents.complete(
    agent_id=agent_id,
    messages=[
        {
            "role": "user",
            "content": f"title: {post['title']},body: {post['selftext']}",
        },
    ],
)
    response = eval(chat_response.choices[0].message.content)
    post['response'] = response['message']
    print(f'title:{post['title']},response:{response['message']}')
    update_post(post)    

In [31]:
import asyncio

async def response_gen(post, agent_id):
    chat_response = await client.agents.complete(
        agent_id=agent_id,
        messages=[
            {
                "role": "user",
                "content": f"title: {post['title']}, body: {post['selftext']}",
            },
        ],
    )
    response = eval(chat_response.choices[0].message.content)
    post['response'] = response['message']
    print(f'title: {post["title"]}, response: {response["message"]}')
    await update_post(post)


async def process_posts(rec, agent_id):
    tasks = [response_gen(post, agent_id) for post in rec]
    await asyncio.gather(*tasks)

# Run the async function
asyncio.run(process_posts(rec, agent_id))


RuntimeError: asyncio.run() cannot be called from a running event loop

Batch Interface 

Prompts

In [16]:
base_prompt = "you are a data analyst who is performing feature engineering you are provided with a title and body of a redddit post you have to validate the post if it is valid to consider it as a startup experience. if it is a question raised by the user mark it as a question else keep it as a experience. Note: Some  Post are like service promotions we would like to ignore those data, Some of the user share their experience and understand the context as they might be seeking for help by sharing their current scenario  flags are ['experience,'question','promotion'].The output format should be {'message':'flag'}"
examples = [
    {
        'user_input':
    {'title':'To all indie app devs who raised funding !',
     'body':"""Did you raise money basis \n1 - just the idea\n2- working app on App Store\n3 - after a certain number of users started using the app\n\nAnd to those who did raise funding via #2 or 3, how did you demo the app, like did you just send the link to the app store (assuming you were in touch with that person/co) or maybe cold reachout \n\nOr you sent a deck with the usual bells and whistles?""",
     },
    'model output': {'message':'question'}
    },
    {
        'user_input':
            {'title':'An Inspiring Startup Story with a Twist',
'body':"""**It started with a trip.**\n\nIn the spring of 2023, a startup founder &amp; CEO boarded a flight to Silicon Valley. At that time, AI for startups felt more like a buzzword than a business necessity. For his fast-growing startup, it seemed smarter to stick to proven strategies, keep costs lean, and avoid distractions.\xa0\n\n“Let the early adopters gamble,” he thought. “We’ll step in later if AI turns out to be more than just a trend.”\n\nBut Silicon Valley has a way of flipping your perspective.\n\nOver the next few days of meetings, coffees and late-night conversations with seasoned founders, investors, and technologists, this CEO heard a message he couldn’t ignore. These weren’t just dreamers — they were doers and builders with a track record of spotting paradigm shifts before they happened.\xa0\n\nAnd they all agreed on one thing:\xa0\n\n**AI isn’t a trend — it’s the next big shift.**\n\nThey compared it to the internet boom of the ’90s and the rise of smartphones in the 2000s. “This isn’t about efficiency,” one founder told him. “It’s about survival. If you’re not using AI, you’re already behind.”\n\nBy the time his plane touched back down, he was no longer a skeptic. He had a new mission: bring AI into his business before it was too late.\n\nWithin months, his company had completely transformed. They reorganized teams, launched AI experiments, and rewrote their marketing playbook to make AI a cornerstone of their strategy.\xa0\n\nWhat happened next?\n\nBy early 2024, his company had transformed:\n\n* **3.3 billion ad impressions**\xa0driven by AI-powered campaigns.\n* **40% better ROI**\xa0on video ads, while cutting production costs.\n* **Freed-up resources**\xa0for bold, creative projects that scaled their impact.\n\nThat CEO is Anton Pavlovsky, and the\xa0company in the story is Headway, a Ukrainian edtech startup leading the way in AI-driven growth.\n\nBut this story isn’t just about Headway. It’s about what AI can do for your business—if you start today."""},
            
    'model output': {'message':'experience'}
    },
]

Dataset Preparation 

In [41]:
def create_chunks(data, chunk_size):
    for i in range(0, len(data), chunk_size):
        yield data[i:i + chunk_size]

chunks = list(create_chunks(rec, 1000))
print(f'Number of chunks: {len(chunks)}')
print(f'Size of first chunk: {len(chunks[0])}')

Number of chunks: 11
Size of first chunk: 1000


In [ ]:
chunks[-1]

In [46]:
for ids in range(len(chunks)):    
    with open(f'./batch_files/batch_data_{ids}.jsonl','a') as f:
        for i in rec:
            dataset = {}
            post_data = {'title':i['title'],'body':i['selftext']}
            dataset['post_id'] = i['id']
            dataset['body'] = {
                "max_tokens": 100,
                "message": [{
                    "role": "user",
                    "content": f" you are provided with the system instructions {base_prompt}, here are some examples {examples} and you are provided with the post title and body {post_data}",
                }]
            }
            f.write(json.dumps(dataset)+'\n')

new batch files

In [14]:
len(rec)

10001

In [15]:
def create_chunks(data, chunk_size):
    for i in range(0, len(data), chunk_size):
        yield data[i:i + chunk_size]

chunks = list(create_chunks( rec, 100))
chunks  = chunks[:-1]
print(f'Number of chunks: {len(chunks)}')
print(f'Size of first chunk: {len(chunks[0])}')

Number of chunks: 100
Size of first chunk: 100


In [11]:
len(chunks[0])

100

In [17]:
for ids in range(len(chunks)):    
    with open(f'./small_batch_files/batch_data_{ids}.jsonl','a') as f:
        for i in rec:
            dataset = {}
            post_data = {'title':i['title'],'body':i['selftext']}
            dataset['post_id'] = i['id']
            dataset['body'] = {
                "max_tokens": 100,
                "message": [{
                    "role": "user",
                    "content": f" you are provided with the system instructions {base_prompt}, here are some examples {examples} and you are provided with the post title and body {post_data}",
                }]
            }
            f.write(json.dumps(dataset)+'\n')

uploading batch data

In [21]:
res = open(f'small_batch_files/batch_data_0.jsonl','rb')
output = res.readlines()


batch_data = client.files.upload(
    file={
        "file_name":"batch_data_0.jsonl",
        "content":res,
    },
    purpose="batch"
)

SDKError: API error occurred: Status 422
{"detail": "Invalid file format.", "description": "Found at least 549 errors in this file. You can view supported formats here: https://docs.mistral.ai/capabilities/finetuning. ", "errors": [{"message": "19 validation errors for BatchMessages\nbody.function-after[has_tool_execution_data_for_all_tools(), ChatCompletionRequest].messages\n  Field required [type=missing, input_value={'max_tokens': 100, 'mess...lp.\"}'}], 'model': None}, input_type=dict]\n    For further information visit https://errors.pydantic.dev/2.9/v/missing\nbody.function-after[has_tool_execution_data_for_all_tools(), ChatCompletionRequest].message\n  Extra inputs are not permitted [type=extra_forbidden, input_value=[{'role': 'user', 'conten...ncers? I need help.\"}'}], input_type=list]\n    For further information visit https://errors.pydantic.dev/2.9/v/extra_forbidden\nbody.ClassificationRequest.input\n  Field required [type=missing, input_value={'max_tokens': 100, 'mess...lp

Google Gemini Approach

In [53]:
import google.generativeai as genai
genai.configure(api_key = gen_ai_key)
model = genai.GenerativeModel("gemini-1.5-flash", system_instruction=f"{base_prompt} Here are some examples {examples}")
response = model.generate_content(f"context: {chunks[0][0]['title']} {chunks[0][0]['selftext']}")
print(response.text)

```json
{'message': 'question'}
```

